In [3]:
# %pip install sagemaker --upgrade --quiet 
# !pip install folium

In [20]:
import pandas as pd
import numpy as np
import sagemaker
import boto3
from sklearn.externals import joblib

import sagemaker
from sagemaker import get_execution_role
from sagemaker.amazon.amazon_estimator import get_image_uri
# from sagemaker.inputs import TrainingInput
# from sagemaker.amazon.amazon_estimator import get_image_uri 
# from sagemaker.session import s3_input, Session     

import matplotlib.pyplot as plt 
import seaborn as sns
import folium
import src.comercio
from sklearn.preprocessing import LabelEncoder
from sklearn.cluster import DBSCAN
import warnings
warnings.filterwarnings("ignore")

In [38]:
# bucket_name = 'comercios-denue'
# # set an output path where the trained model will be saved
# #prefix = 'DBSCAN-clustering'
# #output_path ='/{}/{}/output'.format(bucket_name, prefix)
# output_path ='output'.format(bucket_name)
# print(output_path)

output


In [6]:
bucket_name = 'comercios-denue'
s3_key = 'salidas/denue.csv'

s3 = boto3.client('s3')
obj = s3.get_object(Bucket=bucket_name, Key=s3_key)
df_t = pd.read_csv(obj['Body'])

In [7]:
df_t.head()

id               nom_estab               raz_social  codigo_act  \
0  6981122      EMBOBINADOS DAVILA                      NaN      811312   
1  6981121             DESECHABLES                      NaN      465914   
2  6981120          ROPA AMERICANA                      NaN      465215   
3  6981119  ACCESORIOS Y NOVEDADES  ACCESORIOS Y NOVEDADES       463213   
4  6981114      PENSION MADAGASCAR                      NaN      812990   

                                          nombre_act  per_ocu tipo_vial  \
0  Reparación y mantenimiento de maquinaria y equ...        1     CALLE   
1     Comercio al por menor de artículos desechables        1     CALLE   
2  Comercio al por menor de artículos y aparatos ...        1     CALLE   
3                  Comercio al por menor de lencería        1     CALLE   
4                         Otros servicios personales        1     CALLE   

        nom_vial    tipo_v_e_1          nom_v_e_1  ...  ageb manzana  \
0          SALUD  PROLONGACION  AVENIDA POLIDUCTO  ...  2668       2   
1          SALUD  PROLONGACION  AVENIDA POLIDUCTO  ...  2668       2   
2          SALUD  PROLONGACION  AVENIDA POLIDUCTO  ...  2668       2   
3          SALUD  PROLONGACION  AVENIDA POLIDUCTO  ...  2668       2   
4  AURORA BOREAL       AVENIDA   MARIANO ESCOBEDO  ...  2475      20   

       telefono                   correoelec  www tipoUniEco    latitud  \
0  4492758040.0  EMBOBINADOSDAVILA@GMAIL.COM  NaN        NaN  21.869575   
1  4493692373.0                          NaN  NaN        NaN  21.869584   
2  4493863851.0                          NaN  NaN        NaN  21.869693   
3  4493890114.0                          NaN  NaN        NaN  21.869895   
4  4494485486.0                          NaN  NaN        NaN  21.861681   

     longitud  fecha_alta es_esencial  
0 -102.243051     2019-11           0  
1 -102.243079     2019-11           0  
2 -102.243406     2019-11           0  
3 -102.244008     2019-11           0  
4 -102.273371     2019-11           0  

[5 rows x 42 columns]

# Ejemplo localización solo Querétaro

In [9]:
level_col = ['tipo_vial','nombre_act']
encoder = LabelEncoder()
df_t2 = df_t.copy()
for col in level_col:
    df_t2[col+'_encode'] = encoder.fit_transform(df_t2[col].astype(str))

In [10]:
df_t2_queretaro = df_t2[(df_t2['entidad']=='Querétaro')&(df_t2['municipio']=='Querétaro')]

In [11]:
m = folium.Map(location=[19.344720000, -99.199660000], zoom_start=6)
for _,row in df_t2_queretaro.iterrows():
    folium.Circle(location=[float(row['latitud']),float(row['longitud'])],
                    radius=row['per_ocu']
                   ).add_to(m)

In [12]:
m

In [15]:
objetivo = ['tipo_vial_encode','nombre_act_encode','per_ocu']
df_t2_queretaro[objetivo].hist(xlabelsize=8, figsize =(12,10),color = 'blue', alpha=0.7)

array([[<matplotlib.axes._subplots.AxesSubplot object at 0x7f575ab9e750>,
      dtype=object)

In [16]:
matriz = df_t2_queretaro[objetivo].corr(method='spearman')
plt.figure(figsize=(20, 12))
mask = np.zeros_like(matriz)
mask[np.triu_indices_from(mask)] = True
with sns.axes_style('white'):
    sns.heatmap(matriz,yticklabels = list(matriz),xticklabels= list(matriz), cmap = 'YlGnBu',square = True,mask = mask,annot = True)
plt.title('Matrix Correlation',fontsize = 14)

Text(0.5, 1, 'Matrix Correlation')

# Modelo

In [22]:
df_t3_queretaro = df_t2_queretaro[objetivo].dropna()
df_t3_queretaro.count()

tipo_vial_encode     13440
nombre_act_encode    13440
per_ocu              13440
dtype: int64

In [17]:
# Get the SageMaker execution role
role = get_execution_role()

In [23]:
dbsc = DBSCAN(eps=0.001, min_samples=5)
dbsc.fit(df_t3_queretaro)

DBSCAN(algorithm='auto', eps=0.001, leaf_size=30, metric='euclidean',
       metric_params=None, min_samples=5, n_jobs=None, p=None)

In [24]:
# Save the trained model
joblib.dump(dbsc, 'dbscan_model.joblib')

['dbscan_model.joblib']

In [25]:
# Load the saved model
dbsc_loaded = joblib.load('dbscan_model.joblib')

# Make predictions
labels = dbsc_loaded.labels_


In [27]:
len(np.unique(labels))

446

In [28]:
n_clusters_ = len(set(labels)) - (1 if -1 in labels else 0)
n_noise_ = list(labels).count(-1)

print('Estimated number of clusters: %d' % n_clusters_)
print('Estimated number of noise points: %d' % n_noise_)
print("Silhouette Coefficient: %0.3f"
      % src.comercio.silhouette_score(df_t3_queretaro, labels))

Estimated number of clusters: 445
Estimated number of noise points: 2785
Silhouette Coefficient: 0.590


In [30]:
# Create a new DataFrame with the original data and cluster labels
base_etiquetada = df_t2_queretaro.join(pd.DataFrame({'etiqueta':labels},index = df_t3_queretaro.index))
# Save the DataFrame to a CSV file
base_etiquetada.to_csv('base_etiquetada.csv', index=False)



In [39]:
#Escribir salida en S3
s3 = boto3.client('s3')
s3.upload_file('base_etiquetada.csv', bucket_name, 'salida_modelo/base_etiquetada.csv')

In [29]:
identified_clusters = dbsc_loaded.fit_predict(df_t3_queretaro)
identified_clusters

array([ 0,  1,  2, ..., -1, -1, -1])

In [40]:
dbscan_image_uri = sagemaker.image_uris.retrieve('dbscan', region=sagemaker.Session().boto_region_name)

FileNotFoundError: [Errno 2] No such file or directory: '/opt/conda/lib/python3.7/site-packages/sagemaker/image_uri_config/dbscan.json'

In [19]:
# Set up the SageMaker DBSCAN estimator
dbscan_image_uri = sagemaker.image_uris.retrieve('dbscan', region=sagemaker.Session().boto_region_name)
dbscan = sagemaker.estimator.Estimator(dbscan_image_uri,
                                       role=role,
                                       instance_count=1,
                                       instance_type='ml.c4.xlarge',
                                       output_path=output_path)

FileNotFoundError: [Errno 2] No such file or directory: '/opt/conda/lib/python3.7/site-packages/sagemaker/image_uri_config/dbscan.json'